In [1]:
#Import Statements
import numpy as np
import scipy.special
import mnist_loader
import random

In [2]:
class Network:
    #Construcutor
    def __init__(self,neurons):
        self.layers = len(neurons)
        self.neurons = neurons
        
        self.weights = []
        self.biases = []
        
        #Initialize weights
        for i in range(1,self.layers):
            #layer_weight = None
            rows  = neurons[i]
            cols = neurons[i-1]
            #Creates a numpy array with dimensions rows x cols
            #At the same time, initializes them with random normal distribution b/w 0 and 1
            
            #layer_weight = np.zeros((rows,cols))
            layer_weight = np.random.randn(rows,cols)
            self.weights.append(layer_weight)

            #layer_bias = np.zeros((rows,1))
            layer_bias = np.random.randn(rows,1)
            self.biases.append(layer_bias)

In [3]:
def sigmoid(z):
    return 1.0/(1.0 + scipy.special.expit(-z))

In [4]:
def feedforward(network,X):
    
    #Stores the Aj values
    Layer_Activations = []
    
    #Stores the Zj values
    Weighted_Sums = []
    
    for i in range(1,network.layers):
   
        if i==1:
            A = X
        else:
            A  = Layer_Activations[-1]
        
        W = network.weights[i-1]
        B = network.biases[i-1]
        Z = np.dot(W,A) + B
        Weighted_Sums.append(Z)
        A = sigmoid(Z)
        Layer_Activations.append(A)

    return (Weighted_Sums,Layer_Activations)

In [5]:
def test(network,test_data):

    _,activations = feedforward(network,test_data[0])
    
    Output = activations[-1]
    Target = test_data[1]
    
    #Output --> (10,Number_of_training_Samples)
    #Target --> (Number_of_traing_Samples)
    
    Prediction = np.argmax(Output,axis=0)
    #Prediction --> (Number_of_training_Samples,)    
    
    accuracy = (sum((Prediction == Target).astype(np.float32))/Target.shape[0])*100.0
    
    return accuracy

In [6]:
def sigmoid_derivative(z):
    #print("sigmoid_derivative =",sigmoid(z)*(1-sigmoid(z)) )
    return sigmoid(z)*(1-sigmoid(z))
    

In [7]:
def cost_gradient(output,label):
    #print("cost_gradient =",output-label)
    return output-label

In [8]:
def backprop(network,delta_output_layer,weighted_sums):
    #Initialize error for all layers
    #delta is the backpropogation error
    
    #Number of output layers --> first layer is an input layer, hence excluded
    n_out = network.layers-1
    
    delta_all_layers = [None]*(n_out)
    
    delta_all_layers[-1] = delta_output_layer
    
    for i in range(n_out-2,-1,-1):
        delta_all_layers[i] = np.dot(network.weights[i+1].transpose(),delta_all_layers[i+1])*sigmoid_derivative(weighted_sums[i])
            
    return delta_all_layers

In [9]:
def update_weights(network,X,layer_activations,delta_all_layers,alpha):
    
    before_weight = np.array(network.weights[0],copy=True)
    
    n_weights = network.layers-1
    for i in range(n_weights):
        
        #print("shape of delta_all_layers[",i,"]:",delta_all_layers[i].shape)
        #print("shape of layer_activations[",i,"].transpose():",delta_all_layers[i].transpose().shape)            
        if i==0:
            layer_input = X
        else:
            layer_input = layer_activations[i-1]
        
        print("delta for layer {0} = {1}".format(i,delta_all_layers))

        dcdw = np.dot(delta_all_layers[i],layer_input.transpose())
        dcb = np.average(delta_all_layers[i],axis=1).reshape(delta_all_layers[i].shape[0],1)
        #print("shape of dcdw:",dcdw.shape)
        #print("shape of dcb:",dcb.shape)
        #print("shape of network.weights[",i,"]:",network.weights[i].shape)
        
        print("dcdw for layer {0} = {1}".format(i,dcdw))
        print("dcb for layer {0} = {1}".format(i,dcb))
        network.weights[i] -= alpha * dcdw
        network.biases[i] -= alpha * dcb
    
    if np.array_equal(network.weights[0],before_weight):
        print("No update")
    return

In [10]:
def train_GD(network,train_data,valid_data,mini_batch_size=100,alpha=1,epochs=50):
    
    X = train_data[0] #(784,50000)
    y = train_data[1] #(10,50000)
    #print(X.shape,y.shape)
    
    alpha = alpha/float(mini_batch_size)
    
    for e in range(epochs):

        Xtrans = X.transpose()
        ytrans = y.transpose()
        #print("Xtrans[0].shape",Xtrans[0].shape)
        #print("ytrans[0].shape",ytrans[0].shape)
        #print("Xtrans[0].reshape(X.shape[0],1).shape",Xtrans[0].reshape(X.shape[0],1).shape)
        
        #------------------Al right----------------#
        training_list = [ [ Xtrans[i],ytrans[i] ] for i in range(X.shape[1]) ]

        random.shuffle(training_list)
        
        for k1 in range(0,len(training_list),mini_batch_size):

            #list --> subset of training_list
            training_batch = training_list[k1:k1+mini_batch_size]

            
            Xbatch = np.array([sample[0] for sample in training_batch]).transpose()
            
            ybatch = np.array([sample[1] for sample in training_batch]).transpose()
            
            #print("Dimensions of Xbathc,ybatch ->",Xbatch.shape, ybatch.shape)
            #Step 1: Calculate Output
            weighted_sums,activations = feedforward(network,Xbatch)

            #Step 2: Calculate Error at final layer
            delta_output_layer = cost_gradient(activations[-1],ybatch)*sigmoid_derivative(weighted_sums[-1])

            #Step 3: Backpropogate Error
            delta_all_layers = backprop(network,delta_output_layer,weighted_sums)

            #Step 4: Update Weights
            update_weights(network,Xbatch,activations,delta_all_layers,1)

        #Step 5: Validation Testing
        accuracy = test(network,valid_data)

        print("End of Epoch",e," accuracy =",accuracy)
    
    return

In [11]:
train_data,valid_data,test_data = mnist_loader.load_data_wrapper()
network = Network([784,30,10])
train_GD(network,train_data,valid_data,mini_batch_size=10,alpha=0.1,epochs=100)
#accuracy = test(network,test_data)
print("On Testing Data: Accuracy =",accuracy)

delta for layer 0 = [array([[ -6.97436306e-02,  -1.25998839e-02,   3.93183402e-02,
          1.31989960e-02,  -9.96339264e-02,   3.33472370e-03,
         -1.94941066e-04,  -5.44954341e-02,  -4.81982654e-02,
          1.83066376e-02],
       [  9.17725434e-02,   4.19213204e-02,   3.53285852e-02,
          5.42155351e-02,   2.04719177e-03,   2.03841628e-02,
          5.52215240e-03,   4.62905807e-02,   7.40384070e-02,
          4.74156033e-02],
       [ -8.55399135e-03,  -3.38803922e-02,  -4.97007188e-02,
         -5.58138039e-02,   6.82295902e-02,   9.11594498e-05,
          5.34248774e-02,  -3.19538975e-03,  -1.92888794e-02,
         -5.11777429e-02],
       [  1.65452874e-03,   6.96397197e-02,   2.86313558e-02,
          3.97042677e-02,   1.74661357e-02,  -2.11811024e-05,
          1.93896796e-02,   1.02005010e-01,   1.08483334e-01,
          2.39890438e-02],
       [ -4.09287511e-02,  -1.45497880e-01,  -1.02057456e-01,
         -8.53193551e-02,  -1.55045803e-01,  -2.83367896e-02,
   

dcb for layer 0 = [[ -5.23641261e-08]
 [ -4.53476041e-06]
 [ -7.34528305e-06]
 [ -6.14965761e-04]
 [ -3.10840779e-10]
 [ -4.00542629e-09]
 [ -1.26686235e-13]
 [ -1.72336896e-11]
 [ -1.98452943e-16]
 [ -3.02619046e-14]
 [ -6.96511655e-12]
 [ -1.50896811e-07]
 [ -5.32972351e-09]
 [ -3.09950017e-08]
 [ -1.05515972e-12]
 [ -4.46549810e-16]
 [ -5.27036786e-10]
 [ -1.12659505e-08]
 [ -2.58290403e-04]
 [ -7.41167198e-08]
 [ -1.82473130e-05]
 [ -2.96966639e-08]
 [ -1.64706151e-07]
 [ -1.89784520e-07]
 [ -7.41296354e-09]
 [ -8.21430866e-07]
 [ -7.29549406e-11]
 [ -1.68524827e-12]
 [ -2.32666040e-12]
 [ -3.05613359e-04]]
delta for layer 1 = [array([[ -1.66465368e-08,  -5.55958317e-13,  -1.29348100e-09,
         -9.80823544e-13,  -0.00000000e+00,  -6.44590285e-15,
         -0.00000000e+00,  -0.00000000e+00,  -9.64736793e-13,
         -5.05698735e-07],
       [ -1.77223285e-07,  -8.94286256e-14,  -1.29148614e-12,
         -3.27213658e-10,  -0.00000000e+00,  -3.25457554e-14,
         -0.00000000e+0

delta for layer 0 = [array([[ -1.19465384e-13,  -2.37136834e-14,  -0.00000000e+00,
         -0.00000000e+00,  -2.31707295e-11,  -2.57695804e-02,
         -1.78771088e-09,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -1.78298570e-07,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -1.79785725e-12,  -2.67859788e-06,
         -1.17825959e-09,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -2.99569941e-13,  -0.00000000e+00,  -0.00000000e+00,
         -1.40348406e-14,  -5.47895186e-10,  -2.64457818e-03,
         -5.20297745e-09,  -4.84592937e-15,  -2.20799477e-11,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -6.11786141e-08,  -3.68967542e-08,  -0.00000000e+00,
         -3.47120511e-13,  -5.48086024e-13,  -4.11116258e-02,
   

dcdw for layer 0 = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 ..., 
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
dcb for layer 0 = [[ -3.85806729e-08]
 [  0.00000000e+00]
 [ -4.81734662e-09]
 [  0.00000000e+00]
 [ -4.66394007e-09]
 [ -1.20564210e-11]
 [ -1.29116754e-13]
 [ -2.56308771e-09]
 [  0.00000000e+00]
 [ -2.96313123e-15]
 [ -2.93959701e-11]
 [  0.00000000e+00]
 [ -3.40899781e-08]
 [  0.00000000e+00]
 [  0.00000000e+00]
 [  0.00000000e+00]
 [ -4.24814925e-06]
 [ -9.04645093e-09]
 [ -4.53026406e-08]
 [ -6.56454678e-09]
 [ -2.49077934e-08]
 [ -1.44913424e-09]
 [ -1.14184884e-07]
 [  0.00000000e+00]
 [ -9.45273984e-09]
 [  0.00000000e+00]
 [ -8.51230220e-10]
 [ -4.29007239e-12]
 [ -1.40369303e-12]
 [ -7.52771311e-09]]
delta for layer 1 = [array([[ -0.00000000e+00,  -9.18963227e-13,  -1.49739513e-13,
         -0.00000000e+00,  -1.54263440e-10,  -0.00000000e+00,
         -0.00000

delta for layer 0 = [array([[ -0.00000000e+00,  -0.00000000e+00,  -2.52181473e-13,
         -1.08528049e-06,  -2.84376658e-14,  -0.00000000e+00,
         -1.95489623e-14,  -0.00000000e+00,  -9.49628452e-11,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -1.93205730e-14,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -9.71701446e-15,  -0.00000000e+00,  -9.52459806e-15,
         -6.76355815e-07,  -4.83697772e-12,  -0.00000000e+00,
         -0.00000000e+00,  -1.81301798e-07,  -4.33524792e-08,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -2.55514126e-11,
         -9.40709781e-06,  -6.93914754e-12,  -1.37578253e-09,
   

...

dcb for layer 1 = [[ 0.125]
 [ 0.125]
 [ 0.1  ]
 [ 0.025]
 [ 0.075]
 [ 0.125]
 [ 0.1  ]
 [ 0.125]
 [ 0.075]
 [ 0.125]]
delta for layer 0 = [array([[ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -7.77779271e-14,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -1.23165229e-06,  -3.09295464e-13,
         -1.01996220e-08],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -5.41122940e-13],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -5.92962062e-11,
         -0.00000000e+00],
       [

 [ -1.40730739e-09]]
delta for layer 1 = [array([[ -1.62998951e-09,  -1.04337632e-12,  -0.00000000e+00,
         -0.00000000e+00,  -7.38912827e-10,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -2.79357368e-11,
         -0.00000000e+00],
       [ -1.61762187e-13,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -8.09841112e-14,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -8.09963698e-14,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00, 

delta for layer 0 = [array([[ -0.00000000e+00,  -3.29994449e-13,  -0.00000000e+00,
         -8.26906639e-14,  -6.02842095e-10,  -1.14272357e-05,
         -7.32927875e-12,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00],
       [ -0.00000000e+00,  -0.00000000e+00,  -0.00000000e+00,
         -0.00000000e+00,  -0.00000000e+00,  -8.27160765e-14,
   

         0.125,  0.125]])]
dcdw for layer 0 = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 ..., 
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
dcb for layer 0 = [[ -5.23659804e-07]
 [ -8.60201365e-11]
 [ -4.90821175e-11]
 [  0.00000000e+00]
 [  0.00000000e+00]
 [ -1.08105785e-08]
 [ -1.90587398e-05]
 [  0.00000000e+00]
 [ -5.53804876e-09]
 [ -4.80872871e-11]
 [ -2.46354515e-07]
 [  0.00000000e+00]
 [  0.00000000e+00]
 [ -5.67695736e-07]
 [ -1.44524908e-07]
 [ -8.66781535e-08]
 [ -6.95740967e-13]
 [ -1.15702351e-10]
 [ -3.67303534e-04]
 [  0.00000000e+00]
 [ -2.32447371e-10]
 [ -2.51348640e-05]
 [ -1.94527460e-07]
 [ -3.67250072e-08]
 [ -1.94636586e-07]
 [ -1.71527828e-14]
 [ -6.25624094e-08]
 [ -5.53501359e-06]
 [ -1.29946529e-08]
 [ -4.96136937e-08]]
delta for layer 1 = [array([[ -0.00000000e+00,  -0.00000000e+00,  -1.76810466e-10,
         -0.00000000e+00,  -0.00000000e+00,  -0.0000

KeyboardInterrupt: 